In [55]:
import lzma
import pickle
import cProfile
import pstats

import scipy.stats
from sc2.game_info import GameInfo

import numpy as np
from scipy import ndimage, signal, spatial, stats
from skimage.measure import block_reduce
import plotly.express as px
import plotly.graph_objects as go

In [56]:
import sys
sys.path.append("../bot")

from utils.dijkstra import Point, shortest_paths_opt, DijkstraOutput

In [57]:
with lzma.open("../resources/GresvanAIE.xz", "rb") as f:
    game_info: GameInfo = pickle.load(f)

In [58]:
pathing = game_info.pathing_grid.data_numpy.T
cost = np.where(pathing == 1, 1.0, np.inf)
px.imshow(pathing)

In [59]:
lancester_sigma = 5
lancester_min = 1 - 2 * (1 - stats.norm.cdf(0.5, loc=0, scale=lancester_sigma))
lancester_min = 0.5
lancester_min, np.log(lancester_min)

(0.5, -0.6931471805599453)

In [60]:
m = np.log(lancester_min)
pathing_filtered = ndimage.gaussian_filter(pathing.astype(float), lancester_sigma)
alpha = (np.log(pathing_filtered) - m) / (0 - m)
e = np.where(pathing, 1 + alpha, np.nan)
np.nanmin(e), np.nanmax(e), np.nanmean(e), np.nanstd(e)

C:\Users\volke\AppData\Local\Temp\ipykernel_25656\45955369.py:3: RuntimeWarning:

divide by zero encountered in log



(0.4307138188842635, 1.9904774118972806, 1.620013177884922, 0.2619933511790193)

In [76]:
alpha = 1 + ndimage.gaussian_filter(game_info.pathing_grid.data_numpy.T.astype(float), sigma=lancester_sigma) ** 2
px.imshow(np.where(pathing, alpha, np.nan))

In [74]:
px.imshow(np.where(pathing, alpha, np.nan))

In [77]:
px.histogram(np.where(pathing, alpha, np.nan).flatten())

In [64]:
np.random.seed(0)
cost = np.random.rand(*pathing.shape)
cost = ndimage.gaussian_filter(cost, 2)
cost = (cost - np.min(cost)) / (np.max(cost) - np.min(cost))
cost = np.where(pathing == 1, cost, np.inf)
px.imshow(cost)

In [65]:
sources = [Point((p / 2).rounded) for p in game_info.start_locations]
#sources.extend(Point((2 * game_info.map_center - p).rounded) for p in game_info.start_locations)
for _ in range(100):
    sources.append(tuple(np.random.randint((1, 1), np.array(pathing.shape)-1)))
sources

[(19, 60),
 (65, 100),
 (48, 11),
 (151, 94),
 (42, 110),
 (192, 5),
 (104, 117),
 (102, 121),
 (38, 172),
 (139, 51),
 (63, 129),
 (180, 8),
 (79, 148),
 (19, 86),
 (50, 107),
 (133, 53),
 (155, 78),
 (112, 39),
 (130, 3),
 (114, 72),
 (13, 72),
 (31, 11),
 (26, 50),
 (116, 27),
 (99, 47),
 (186, 76),
 (131, 74),
 (197, 38),
 (51, 93),
 (149, 66),
 (195, 119),
 (70, 162),
 (79, 106),
 (113, 141),
 (45, 87),
 (41, 5),
 (140, 169),
 (14, 50),
 (9, 151),
 (73, 48),
 (50, 80),
 (33, 151),
 (97, 171),
 (175, 92),
 (129, 171),
 (139, 135),
 (67, 77),
 (120, 54),
 (192, 139),
 (126, 112),
 (112, 105),
 (50, 60),
 (189, 66),
 (170, 115),
 (197, 1),
 (149, 54),
 (171, 100),
 (27, 99),
 (41, 126),
 (158, 12),
 (157, 163),
 (136, 15),
 (37, 108),
 (6, 159),
 (23, 140),
 (53, 96),
 (53, 162),
 (109, 160),
 (80, 137),
 (57, 173),
 (83, 11),
 (150, 37),
 (16, 102),
 (56, 161),
 (45, 70),
 (107, 72),
 (130, 21),
 (52, 83),
 (44, 156),
 (142, 108),
 (190, 73),
 (49, 171),
 (152, 120),
 (78, 87),
 (19

In [66]:
paths = shortest_paths_opt(cost, sources, diagonal=True)
target = Point(game_info.map_center.rounded)
path = paths.get_path(target)

In [67]:
result = np.where(pathing == 1, 0.0, np.inf)
for x, y in path:
    result[x, y] = 1.0
px.imshow(result)

In [68]:
%%timeit
shortest_paths_opt(cost, sources)

28.9 ms ± 2.8 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [69]:
%%timeit
shortest_paths_opt(cost, sources, diagonal=True)

49.7 ms ± 838 μs per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [70]:
with cProfile.Profile() as prof:
    shortest_paths_opt(cost, sources, diagonal=True)
    stats = pstats.Stats(prof)
stats.sort_stats(pstats.SortKey.CUMULATIVE).print_stats()

         240771 function calls in 0.098 seconds

   Ordered by: cumulative time

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
        1    0.054    0.054    0.100    0.100 C:\Users\volke\PycharmProjects\12PoolBot\bot\utils\dijkstra.py:56(shortest_paths_opt)
    15853    0.017    0.000    0.030    0.000 {built-in method _heapq.heappop}
   174170    0.015    0.000    0.015    0.000 C:\Users\volke\PycharmProjects\12PoolBot\bot\utils\dijkstra.py:19(__lt__)
    11559    0.005    0.000    0.005    0.000 C:\Users\volke\PycharmProjects\12PoolBot\bot\utils\dijkstra.py:47(_neighbours_diagonal)
    15752    0.003    0.000    0.004    0.000 {built-in method _heapq.heappush}
    11559    0.004    0.000    0.004    0.000 C:\Users\volke\PycharmProjects\12PoolBot\bot\utils\dijkstra.py:38(_neighbours)
    11660    0.001    0.000    0.001    0.000 {method 'append' of 'list' objects}
       20    0.000    0.000    0.000    0.000 C:\Users\volke\AppData\Local\pypoetry\Cache\virtu